$\newcommand\N{\mathbb N}
\newcommand\Z{\mathbb Z}
\newcommand\Q{\mathbb Q}
\newcommand\R{\mathbb R}
\newcommand\C{\mathbb C}
\newcommand\too\longrightarrow
\renewcommand\phi\varphi
\renewcommand\epsilon\varepsilon
\renewcommand\hat\widehat
\renewcommand\tilde\widetilde
\renewcommand\vec\overrightarrow
\renewcommand\bar\overline
\newcommand\fl[1]{\left\lfloor #1\right\rfloor}
\newcommand\llbracket{[\![}
\newcommand\rrbracket{]\!]}
\newcommand\bbr[2]{\llbracket #1,#2\rrbracket}
\newcommand\todo{{\bf TODO }}
\newcommand\prob{\mathbb P}
\newcommand\esp{\mathbb E}
\newcommand\var{\mathbb V}
\newcommand\tribu{\mathfrak T}
\newcommand\stirlinga[2]{\left[#1\atop #2\right]}
\newcommand\stirlingb[2]{\left\{#1\atop #2\right\}}$

# Une famille de fonctions définies par des séries

Marc Lorenzi

15 mai 2025

In [ ]:
import matplotlib.pyplot as plt
from fractions import Fraction

**Exercice.** Montrer que la série $\sum_{n\ge 0}n^2/2^n$ converge et calculer sa somme.

Pourquoi étudier un cas particulier quand on peut traiter le cas général ? 

## 1. Introduction

### 1.1 Une série absolument convergente

Notons $D$ le *disque unité ouvert* de $\C$ :

$$D=\{z\in\C:|z|<1\}$$


Soient $p\in\N$ et $z\in D$. Si $z\ne 0$, $n^{p+2}=o(1/|z|^n)$. On a donc pour tout $n\in\N$ assez grand, $n^{p+2}\le \frac 1{|z|^n}$, ou encore

$$n^p|z|^n\le\frac 1{n^2}\text{ (TGSRC)}$$

La série $\sum n^pz^n$ est donc absolument convergente. Bien entendu, cette série est aussi absolument convergente si $z=0$ : tous les termes sont nuls pour $n\ge 1$. Remarquons également que si $|z|\ge 1$, le terme général de la série ne tend pas vers 0, et donc la série diverge grossièrement. Ainsi, la série converge si et seulement si $z\in D$.

Posons pour tout $p\in\N$ et tout $z\in D$,

$$f_p(z)=\sum_{n=0}^\infty n^pz^n$$

Nous venons de définir une fonction $f_p:D\too\C$. L'exercice demande de calculer $f_2(1/2)$.

Remarquons que $f_0(0)=1$ et pour tout $p\ge 1$, $f_p(0)=0$. De plus, pour tout $z\in D$,

$$f_0(z)=\sum_{n=0}^\infty z^n=\frac 1{1-z}$$

La fonction `approx_f` renvoie la $N^e$ somme partielle de la série qui définit $f_p$.

In [ ]:
def approx_f(p, z, N):
    s = 0
    for n in range(N + 1):
        s += n ** p * z ** n
    return s

In [ ]:
print(approx_f(2, 0.5, 100))

Se pourrait-il que $f_2(1/2)=5,999999...$ (c'est à dire 6) ? Oui, et nous allons faire infiniment mieux.

### 1.2 Une relation de récurrence

<div style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;color:#000000;border-radius:10px;" >
    <b>Proposition 1.</b> Pour tout $p\ge 1$ et tout $z\in D$,
$$(1-z)f_p(z)=z\sum_{k=0}^{p-1}\binom p kf_k(z)$$    
</div>

**Démonstration.** Soit $p\ge 1$. L'astuce consiste à poser $n'=n-1$ dans l'expression de $f_p(z)$. On obtient

$$f_p(z)=0^pz^0+\sum_{n=1}^\infty n^pz^n=z\sum_{n=0}^\infty (n+1)^pz^n$$

Par le binôme de Newton et la linéarité de la somme,

$$f_p(z)=z\sum_{n=0}^\infty \sum_{k=0}^p\binom p kn^kz^n=z\sum_{k=0}^p\binom p k\sum_{n=0}^\infty n^kz^n=z\sum_{k=0}^p\binom p kf_k(z)$$

d'où le résultat.

**Remarque.** Le cas $z=1/2$ est particulièrement simple. On a $f_0(1/2)=2$ et pour tout $p\ge 1$,

$$f_p\left(\frac 1 2\right)=\sum_{k=0}^{p-1}\binom p kf_k\left(\frac 1 2\right)$$

Comme nous allons avoir besoin de calculer des coefficients binomiaux, voici une fonction `maj_binom`.Cette fonction prend en paramètre une liste `cs` censée être la liste des $\binom n k$ pour $k\in\bbr0{n-1}$ (où $n\ge 1$). Elle renvoie la liste des $\binom n k$ pour $k\in\bbr0{n}$.  

In [ ]:
def maj_binom(cs):
    n = len(cs)
    return  [1] + [cs[k - 1] + cs[k] for k in range(1, n)] + [1]

In [ ]:
cs = [1]
for k in range(10):
    cs = maj_binom(cs)
    print(k, cs)

La fonction `f` prend un paramètres un entier naturel $p$ et un nombre complexe $z$. Elle renvoie $f_p(z)$.

In [ ]:
def f(p, z):
    ys = [1 / (1 - z)]
    binom = [1]
    for q in range(1, p + 1):
        binom = maj_binom(binom)
        s = 0
        for k in range(q):
            s += binom[k] * ys[k]
        ys.append(s * z / (1 - z))
    return ys[-1]

Qu'obtient-on pour $z=1/2$ ?

In [ ]:
for p in range(21):
    print('%3d%25s' % (p, f(p, Fraction(1, 2))))

En particulier,

$$\sum_{n=0}^\infty\frac{n^2}{2^n}=6$$

Nous pourrions nous arrêter là, mais l'occasion est trop belle. On peut obtenir une valeur « explicite » de $f_p(z)$.

## 2. Une formule explicite pour $f_p(z)$

### 2.1 Nombres de Stirling

Pour tous $n,k\in\N$, le *nombre de Stirling* (de deuxième espèce) $\stirlingb n k$ est le nombre de partitions en $k$ sous-ensembles d'un ensemble de cardinal $n$. Pour tout $n\in\N$, $\stirlingb n 0=\stirlingb 0 n=\delta_{n0}$. On peut montrer que pour tous $n,k\ge 1$,

$$\stirlingb nk=\stirlingb {n-1} {k-1}+k\stirlingb {n-1} {k}$$

Enfin, pour tous $n,k\in\N$ tels que $k>n$, $\stirlingb nk=0$.

La fonction `liste_stirling` renvoie la liste des $\stirlingb N k$ pour $k\in\bbr 0N$.

In [ ]:
def liste_stirling(N):
    ss = (N + 1) * [0]
    ss[0] = 1
    for n in range(1, N + 1):
        ss1 = (N + 1) * [0]
        for p in range(1, n + 1):
            ss1[p] = ss[p - 1] + p * ss[p]
        ss = ss1
    return ss

In [ ]:
for n in range(11):
    print(n, liste_stirling(n))

### 2.2 Puissances descendantes

Soit $a\in \mathbb A$, où $(\mathbb A,+,\times)$ est un anneau quelconque. Pour tout $n\in\N$, la $n^e$ *puissance descendante* de $a$ est

$$a^{\underline n}=\prod_{k=0}^{n-1}(a-k)$$

En particulier, $a^{\underline 0}=1$ (produit vide). En prenant $\mathbb A=\C[X]$ et $a=X$, on obtient la famille de polynômes $\mathcal B'=(X^{\underline n})_{n\in\N}$. Pour tout $n\in\N$, $\deg(X^{\underline n})=n$, donc $\mathcal B'$ est une base de $\C[X]$. Les puissances de $X$ s'écrivent donc de façon unique comme combinaison linéaire des $X^{\underline n}$. Quels sont les coefficients de ces combinaisons linéaires ?

<div style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;color:#000000;border-radius:10px;" >
    <b>Proposition 2.</b> Pour tout $n\in\N$,
    
$$X^n=\sum_{k=0}^n\stirlingb nkX^{\underline k}$$
</div>

**Démonstration.** Calculs, calculs ... la preuve peut être sautée en première lecture ! Montrons l'égalité par récurrence sur $n$. On a $X^0=X^{\underline0}=\stirlingb 00=1$, d'où l'égalité pour $n=0$. Soit $n\ge 1$. Supposons l'égalité vérifiée pour $n-1$. On a

\begin{eqnarray*}
\sum_{k=0}^n\stirlingb n kX^{\underline k}&=&\sum_{k=1}^n\left(\stirlingb {n-1} {k-1}+k\stirlingb {n-1} {k}\right)X^{\underline k}\\
&=&\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline k}+\sum_{k=1}^nk\stirlingb {n-1} {k}X^{\underline k}\\
&=&\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline k}+\sum_{k=0}^{n-1}k\stirlingb {n-1} {k}X^{\underline k}\\
\end{eqnarray*}

Remarquons maintenant que pour tout $k\ge 1$, 

$$X^{\underline k}=X^{\underline{k-1}}(X-(k-1))$$

Le premier terme de la somme ci-dessus s'écrit donc

\begin{eqnarray*}
\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline k}&=&\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline{k-1}}(X-(k-1))\\
&=&X\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline{k-1}}-\sum_{k=1}^n(k-1)\stirlingb {n-1} {k-1}X^{\underline{k-1}}\\
&=&X\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline{k-1}}-\sum_{k=0}^{n-1}k\stirlingb {n-1} {k}X^{\underline{k}}\\
\end{eqnarray*}

De là,

$$\sum_{k=0}^n\stirlingb n kX^{\underline k}=X\sum_{k=1}^n\stirlingb {n-1} {k-1}X^{\underline{k-1}}=X\sum_{k=0}^{n-1}\stirlingb {n-1} {k}X^{\underline{k}}$$

d'où le résultat par l'hypothèse de récurrence.

**Remarque.** Le lecteur se sera sans doute dit que comme la famille $\mathcal B=(X^n)_{n\in\N}$ est une base de $\C[X]$, on peut aussi écrire les polynômes $X^{\underline n}$ de façon unique comme combinaison linéaire des $X^n$. Sans démonstration, on a pour tout $n\in\N$,

$$X^{\underline n}=\sum_{k=0}^n(-1)^{n-k}\stirlinga n kX^k$$

où les entiers $\stirlinga n k$ sont les *nombres de Stirling de première espèce*.

### 2.3 Dérivation

Une récurrence facile sur $p$ montre que pour tous $n,p\in\N$, la dérivée d'ordre $p$ de $X^n$ est

$$(X^n)^{(p)}=n^{\underline p}X^{n-p}$$

Cette égalité est vérifiée même si $p>n$, car dans ce cas, $n^{\underline p}=0$..

Rappelons que $f_0:D\too\C$ est définie pour tout $z\in D$ par 

$$f_0(z)=\frac 1{1-z}=\sum_{n=0}^\infty z^n$$

La fonction $f_0$ est indéfiniment dérivable sur $D$ (au sens complexe. Oui, je sais, je déborde un peu du cadre du cours) . Facilement, pour tout $z\in D$ et tout $p\in\N$,

$$f_0^{(p)}(z)=\frac{p!}{(1-z)^{p+1}}$$

Un théorème sur les *séries entières* que nous admettrons ici montre que pour tout $p\in\N$ et tout $z\in D$, $f_0^{(p)}(z)$ est la somme de la série obtenue en dérivant terme à terme la série qui définit $f_0(z)$ :

$$f_0^{(p)}(z)=\sum_{n=0}^\infty n^{\underline p}z^{n-p}$$

<div style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;color:#000000;border-radius:10px;" >
    <b>Proposition 3.</b> Pour tout $z\in D$ et tout $p\in\N$,
$$f_p(z)=\frac 1{1-z}\sum_{k=0}^pk!\stirlingb p k\left(\frac z{1-z}\right)^k$$    
</div>

Soient $z\in D$ et $p\in\N$. Si $z=0$, l'égalité est trivialement vérifiée. Supposons donc $z\ne 0$. On a

\begin{eqnarray*}
f_p(z)&=&\sum_{n=0}^\infty n^pz^n\\
&=&\sum_{n=0}^\infty\sum_{k=0}^p\stirlingb p kn^{\underline k}z^n\\
&=&\sum_{k=0}^p\stirlingb p k\sum_{n=0}^\infty n^{\underline k}z^n\\
&=&\sum_{k=0}^p\stirlingb p kz^k\sum_{n=0}^\infty n^{\underline k}z^{n-k}\\
&=&\sum_{k=0}^p\stirlingb p kz^kf_0^{(k)}(z)\\
\end{eqnarray*}

d'où le résultat en remplaçant $f_0^{(k)}(z)$ par sa valeur.

**Remarque.** La fonction $f_p$ est une fraction rationnelle. Elle possède un unique pôle, qui est 1. Ce pôle est d'ordre $p+1$. En effet,

$$f_p(z)=\frac{Q_p(z)}{(1-z)^{p+1}}$$

où

$$Q_p=\sum_{k=0}^pk!\stirlingb p kX^k(1-X)^{p-k}\in\C_p[X]$$

Cette écriture est irréductible puisque $Q_p(1)=p!\ne 0$. Une étude plus détaillée de $Q_p$ serait certainement très intéressante (degré ? racines ? etc.).

Le cas $z=1/2$ est particulièrement simple, puisque dans ce cas $1-z=z$.

<div style="border: 1px solid black; padding: 10px;background-color:#CCFFCC;color:#000000;border-radius:10px;" >
    <b>Corollaire 4.</b> Pour tout $p\in\N$,
    
$$\sum_{n=0}^\infty\frac{n^p}{2^n}=2\sum_{k=0}^pk!\stirlingb p k$$
</div>

### 2.4 Python

Tout comme `f`, la fonction `f2` renvoie $f_p(z)$.

In [ ]:
def f2(p, z):
    ss = liste_stirling(p)
    w = z / (1 - z)
    s = 0
    fact = 1
    for k in range(p + 1):
        s += fact * ss[k] * w ** k
        fact *= k + 1
    return s / (1 - z)

Comparons les résultats renvoyés par `f` et par `f2`. Ils devraient évidemment être identiques.

In [ ]:
z = Fraction(1, 2)
for p in range(21):
    print('%3d%25s%25s' % (p, f(p, z), f2(p, z)))

On a tout bon.

Pour terminer, voici le graphe de la restriction de $f_p$ à $]-1,1/2[$ pour quelques valeurs de $p$. Facilement, la fonction $f_p$ est croissante sur $[0,1[$. Son comportement sur $]-1,0]$ est plus compliqué ...

Tous les calculs sont faits de façon exacte : sur $]-1,0]$, les erreurs d'arrondi sur les flottants sont trop importantes pour donner des résultats corrects.

In [ ]:
def subdi_ouverte(a, b, n):
    d = Fraction(b - a, n)
    return [a + k * d for k in range(1, n)]

In [ ]:
plt.rcParams['figure.figsize'] = (8, 4)

In [ ]:
mini = -Fraction(1, 1)
maxi = Fraction(1, 2)
xs = subdi_ouverte(mini, maxi, 1000)
for p in range(0, 10):
    ys = [f2(p, x) for x in xs]
    plt.plot(xs, ys, lw=1)
plt.ylim(-2, 5)
plt.xlim(float(mini), float(maxi))
plt.grid()

Réservons l'étude de $f_p$ sur $]-1,0]$ pour le prochain DS😀.